### A2: Bias in data

### Getting the article and population data

In [1]:
## getting the data from the CSV files
import csv




In [8]:
# reading data and saving in dictionary of dictionaries
'''
{
    "revision_id": {
        "country": "",
        "article_name": "",
        "revision_id":"",
    },
    "revision_id": {
    
    },
    ...
}
'''

page_data = dict()
skip_lines = 1

with open('page_data.csv', encoding="utf8") as csvfile:
    reader = csv.reader(csvfile)
    for row in reader:
        #page_data.append([row[0],row[1],row[2]])
        #['Template:ZambiaProvincialMinisters', 'Zambia', '235107991']
        if(skip_lines!=1):
            revision_id = row[2]
            page_data[revision_id]=dict()
            page_data[revision_id]["country"] = row[1]
            page_data[revision_id]["article_name"] = row[0]
            page_data[revision_id]["revision_id"] = row[2] 
            
        skip_lines = skip_lines+1
print(len((page_data)))

47197


In [18]:

'''
{
    "country_name_1":"population",
    "country_name_1":"population"
}

'''
population_data = {}

# skip twolines from input csv file 
skip_lines = 1
with open('Population Mid-2015.csv', encoding="utf8") as csvfile:
    reader = csv.reader(csvfile)
    for row in reader:
        # last line in the raw data file is an empty line
        # skip_lines > 2 skips first two lines
        # row checks if the read list is empty
        #print(row)
        if(skip_lines>3 and row):
            # ['Afghanistan', 'Country', 'Mid-2015', 'Number', '32,247,000', '']
            population_data[row[0]] = row[4]
        skip_lines = skip_lines + 1
        
print(population_data)

{'Afghanistan': '32,247,000', 'Albania': '2,892,000', 'Algeria': '39,948,000', 'Andorra': '78,000', 'Angola': '25,000,000', 'Antigua and Barbuda': '90,000', 'Argentina': '42,426,000', 'Armenia': '3,017,106', 'Australia': '23,888,000', 'Austria': '8,615,955', 'Azerbaijan': '9,651,000', 'Bahamas': '377,000', 'Bahrain': '1,412,299', 'Bangladesh': '160,411,000', 'Barbados': '278,000', 'Belarus': '9,524,247', 'Belgium': '11,211,064', 'Belize': '368,000', 'Benin': '10,583,034', 'Bhutan': '757,000', 'Bolivia': '10,475,500', 'Bosnia-Herzegovina': '3,650,114', 'Botswana': '2,139,900', 'Brazil': '204,519,398', 'Brunei': '413,000', 'Bulgaria': '7,181,000', 'Burkina Faso': '18,450,400', 'Burundi': '10,742,000', 'Cambodia': '15,417,100', 'Cameroon': '23,739,000', 'Canada': '35,833,000', 'Cape Verde': '514,000', 'Central African Republic': '5,551,900', 'Chad': '13,707,000', 'Channel Islands': '164,000', 'Chile': '18,025,000', 'China': '1,371,920,000', 'Colombia': '48,218,000', 'Comoros': '764,000', 

In [56]:
# merging data set from wikipedia data(page_data) and population data(population_data)
# reading data from page_data and including poulation data
'''
{
    "revision_id": {
        "country": "",
        "article_name": "",
        "revision_id":"",
        "population":""
    },
    "revision_id": {
    
    },
    ...
}
'''
count=0
for key,value in page_data.items():
    revision_id = key
    #print(key)
    
    country_page_data = value["country"]
    #print(country_page_data)
    
    if population_data.get(str(country_page_data)) is not None:
        page_data[revision_id]["population"] = population
    else:
        # for now setting population as 0 for countries which are not preset in population_data
        page_data[revision_id]["population"] = 0
        count = count+1
        
print("no of entries which have popluation  = 0")      
print(count)



no of entries which have popluation  = 0
1397


### Getting article quality predictions

In [106]:
import requests
import json

headers = {'User-Agent' : 'https://github.com/abhishekanand', 'From' : 'anand1@uw.edu'}

def get_ores_data(revision_ids, headers):
    
    # Define the endpoint
    endpoint = 'https://ores.wikimedia.org/v3/scores/{project}/?models={model}&revids={revids}'
    
    # Specify the parameters - smushing all the revision IDs together separated by | marks.
    # Yes, 'smush' is a technical term, trust me I'm a scientist.
    # What do you mean "but people trusting scientists regularly goes horribly wrong" who taught you tha- oh.  
    params = {'project' : 'enwiki',
              'model'   : 'wp10',
              'revids'  : '|'.join(str(x) for x in revision_ids)
              }
    api_call = requests.get(endpoint.format(**params))
    response = api_call.json()
    json.dumps(response, indent=4, sort_keys=True)
    return response


# So if we grab some example revision IDs and turn them into a list and then call get_ores_data...
#example_ids = [783381498, 807355596, 757539710]
#get_ores_data(example_ids, headers)


#get_ores_data(example_ids, headers)
no_revision_ids = len(page_data)
print(no_revision_ids)

# getting all the revision ids from page_data in list format
revision_ids = list(page_data.keys())


counter = 0
call_count = 0

# this contains revsion id as key and article quality as value
data_revision_quality  = {}



# prediction is being added in page_data
'''
{
    "revision_id": {
        "country": "",
        "article_name": "",
        "revision_id":"",
        "population":"",
        "prediction":""
    },
    "revision_id": {
    
    },
    ...
}
'''

while(counter<no_revision_ids and (counter+100)<no_revision_ids):
    temp = get_ores_data(revision_ids[counter:counter+100], headers)
    hundred_revisions = temp["enwiki"]["scores"]
    
    for key, value in hundred_revisions.items():
        revision = key
        prediction = value["wp10"]["score"]["prediction"]
        page_data[revision]["prediction"] = prediction
        print(page_data[revision])
        
        
    counter = counter + 100
    call_count = call_count + 1
    
    
if(counter>no_revision_ids):
    get_ores_data(revision_ids[counter-100:no_revision_ids%100], headers)
    print("hello different")
    

47196
{'country': 'Zambia', 'article_name': 'Template:ZambiaProvincialMinisters', 'revision_id': '235107991', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Chad', 'article_name': 'Bir I of Kanem', 'revision_id': '355319463', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Zimbabwe', 'article_name': 'Template:Zimbabwe-politician-stub', 'revision_id': '391862046', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Uganda', 'article_name': 'Template:Uganda-politician-stub', 'revision_id': '391862070', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Namibia', 'article_name': 'Template:Namibia-politician-stub', 'revision_id': '391862409', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Nigeria', 'article_name': 'Template:Nigeria-politician-stub', 'revision_id': '391862819', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Colombia', 'article_name': 'Template:Colombia-politician-stub', 'revision_id': '391863340

{'country': 'Tanzania', 'article_name': 'Template:Tanzania-mayor-stub', 'revision_id': '446465586', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Tanzania', 'article_name': 'Template:Tanzania-politician-stub', 'revision_id': '446468308', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Sierra Leone', 'article_name': 'Template:SierraLeone-politician-stub', 'revision_id': '447694868', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Sierra Leone', 'article_name': 'Template:SierraLeone-mayor-stub', 'revision_id': '447696094', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Pakistan', 'article_name': 'Sehba Musharraf', 'revision_id': '448555418', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Canada', 'article_name': 'Template:Nunavut-politician-stub', 'revision_id': '450168181', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Croatia', 'article_name': 'Template:Croatia-mayor-stub', 'revision_id': '4557470

{'country': 'Bangladesh', 'article_name': 'Template:Bangladesh-diplomat-stub', 'revision_id': '541009166', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Australia', 'article_name': 'Template:Australia-diplomat-stub', 'revision_id': '541017284', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Philippines', 'article_name': 'Template:Philippines-diplomat-stub', 'revision_id': '541019756', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Turkmenistan', 'article_name': 'Template:Heads of government of Turkmenistan', 'revision_id': '541142538', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Nicaragua', 'article_name': 'Manuel Antonio Blas Sáenz', 'revision_id': '543225630', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Austria', 'article_name': 'Template:Austria-politician-stub', 'revision_id': '544279941', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Algeria', 'article_name': 'Template:Algeria-politic

{'country': 'Ukraine', 'article_name': 'Template:Ukraine-MP-stub', 'revision_id': '603583697', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Croatia', 'article_name': 'Template:Croatia-diplomat-stub', 'revision_id': '605879488', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Tuvalu', 'article_name': 'Template:Prime Minister of Tuvalu', 'revision_id': '607934598', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Pakistan', 'article_name': 'Template:Pakistan-politician-stub', 'revision_id': '610315750', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Somalia', 'article_name': 'Template:Presidents of Somaliland', 'revision_id': '612095066', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Niuean', 'article_name': 'Template:NiuePMs', 'revision_id': '612095385', 'population': 0, 'prediction': 'Stub'}
{'country': 'Antigua and Barbuda', 'article_name': 'Template:Prime Minister of Antigua and Barbuda', 'revision_id': '61280

{'country': 'Yemen', 'article_name': 'Template:Yemen-diplomat-stub', 'revision_id': '647572730', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Gabon', 'article_name': 'Template:Gabon-diplomat-stub', 'revision_id': '647573541', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'China', 'article_name': 'Pan Yunduan', 'revision_id': '647832959', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Finland', 'article_name': 'Otto Elfving', 'revision_id': '647893858', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Lebanon', 'article_name': 'Template:Lebanon-diplomat-stub', 'revision_id': '647908204', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 'Sri Lanka', 'article_name': 'List of Sri Lankan politicians', 'revision_id': '648048611', 'population': '4,832,000', 'prediction': 'Start'}
{'country': 'India', 'article_name': 'Fathema Ismail', 'revision_id': '648271473', 'population': '4,832,000', 'prediction': 'Stub'}
{'country': 

...

{'country': 'Congo, Dem. Rep. of', 'article_name': 'Jean-Pierre Bemba', 'revision_id': '807193274', 'population': '4,832,000', 'prediction': 'GA'}
{'country': 'Greece', 'article_name': 'Tasos Kourakis', 'revision_id': '807193400', 'population': '4,832,000', 'prediction': 'Start'}
{'country': 'Botswana', 'article_name': 'Duma Boko', 'revision_id': '807194059', 'population': '4,832,000', 'prediction': 'C'}
{'country': 'South Africa', 'article_name': 'Winnie Madikizela-Mandela', 'revision_id': '807194252', 'population': '4,832,000', 'prediction': 'B'}
{'country': 'Bangladesh', 'article_name': 'Khaled Mosharraf', 'revision_id': '807195012', 'population': '4,832,000', 'prediction': 'C'}
{'country': 'Australia', 'article_name': 'Gough Whitlam', 'revision_id': '807195226', 'population': '4,832,000', 'prediction': 'FA'}
{'country': 'Australia', 'article_name': 'James Scullin', 'revision_id': '807195799', 'population': '4,832,000', 'prediction': 'FA'}
{'country': 'Pakistan', 'article_name': 'Ca

{'country': 'Tunisia', 'article_name': 'Taïeb Baccouche', 'revision_id': '807241529', 'population': '4,832,000', 'prediction': 'Start'}
{'country': 'Canada', 'article_name': 'James Douglas (governor)', 'revision_id': '807243266', 'population': '4,832,000', 'prediction': 'C'}
{'country': 'Congo, Dem. Rep. of', 'article_name': 'Jason Sendwe', 'revision_id': '807243537', 'population': '4,832,000', 'prediction': 'GA'}
{'country': 'Russia', 'article_name': 'Tatyana Yumasheva', 'revision_id': '807243616', 'population': '4,832,000', 'prediction': 'C'}
{'country': 'Israel', 'article_name': 'Ayelet Shaked', 'revision_id': '807243744', 'population': '4,832,000', 'prediction': 'GA'}
{'country': 'Nigeria', 'article_name': 'Ngozi Okonjo-Iweala', 'revision_id': '807244048', 'population': '4,832,000', 'prediction': 'GA'}
{'country': 'Israel', 'article_name': 'Benjamin Netanyahu', 'revision_id': '807244209', 'population': '4,832,000', 'prediction': 'GA'}
{'country': 'Germany', 'article_name': 'Beatrix

{'country': 'Cape Colony', 'article_name': 'George Grey', 'revision_id': '807290539', 'population': 0, 'prediction': 'GA'}
{'country': 'Japan', 'article_name': 'Shōgun', 'revision_id': '807291575', 'population': '4,832,000', 'prediction': 'C'}
{'country': 'New Zealand', 'article_name': 'John Tamihere', 'revision_id': '807291733', 'population': '4,832,000', 'prediction': 'C'}
{'country': 'United Kingdom', 'article_name': 'Chris Huhne', 'revision_id': '807292420', 'population': '4,832,000', 'prediction': 'B'}
{'country': 'Australia', 'article_name': 'Sam Loxton', 'revision_id': '807292621', 'population': '4,832,000', 'prediction': 'FA'}
{'country': 'Russia', 'article_name': 'Lavrentiy Beria', 'revision_id': '807293910', 'population': '4,832,000', 'prediction': 'B'}
{'country': 'United Kingdom', 'article_name': 'Herbert Stern, 1st Baron Michelham', 'revision_id': '807295005', 'population': '4,832,000', 'prediction': 'Start'}
{'country': 'China', 'article_name': 'Li Keqiang', 'revision_id'

{'country': 'Russia', 'article_name': 'Joseph Stalin', 'revision_id': '807340998', 'population': '4,832,000', 'prediction': 'FA'}
{'country': 'Portugal', 'article_name': 'Armando Vara', 'revision_id': '807341268', 'population': '4,832,000', 'prediction': 'Start'}
{'country': 'United States', 'article_name': 'Stuart M. Gerson', 'revision_id': '807341393', 'population': '4,832,000', 'prediction': 'Start'}
{'country': 'India', 'article_name': 'Mohammad Shafi Qureshi', 'revision_id': '807341484', 'population': '4,832,000', 'prediction': 'Start'}
{'country': 'Russia', 'article_name': 'Marat Safin', 'revision_id': '807343155', 'population': '4,832,000', 'prediction': 'B'}
{'country': 'Russia', 'article_name': 'Natalya Narochnitskaya', 'revision_id': '807343220', 'population': '4,832,000', 'prediction': 'Start'}
{'country': 'Austria', 'article_name': 'Julius Deutsch', 'revision_id': '807343840', 'population': '4,832,000', 'prediction': 'Start'}
{'country': 'Saudi Arabia', 'article_name': 'Niz

KeyError: 'score'